In [1]:
import logging
logging.root.handlers = []  # Jupyter messes up logging so needs a reset
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
from smart_open import smart_open
import pandas as pd
import numpy as np
from numpy import random
import gensim
import nltk
from sklearn.cross_validation import train_test_split
from sklearn import linear_model
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics import accuracy_score, confusion_matrix
import matplotlib.pyplot as plt
from gensim.models import Word2Vec
from sklearn.neighbors import KNeighborsClassifier
from sklearn import linear_model
from nltk.corpus import stopwords
import os, codecs
%matplotlib inline
from bs4 import BeautifulSoup
import re
from nltk.corpus import stopwords
from sklearn import metrics as skmetrics
import seaborn as sns; sns.set()
import scipy.stats

2017-08-12 14:26:08,725 : INFO : 'pattern' package found; tag filters are available for English
/usr/lib64/python2.7/site-packages/sklearn/cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
pd.set_option('display.max_rows', 5000)
pd.reset_option('display.max_rows')

## Model 1 evaluation

In [3]:
df = pd.read_csv('~/personality-normalized-single-file-word2vec.csv', encoding='utf-8')
df.shape

/usr/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2717: DtypeWarning: Columns (9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79,80,81,82,83,84,85,86,87,88,89,90,91,92,93,94,95,96,97,98,99,100,101,102,103,104,105,106,107,108,109,110,111,112,113,114,115,116,117,118,119,120,121,122,123,124,125,126,127,128,129,130,131,132,133,134,135,136,137,138,139,140,141,142,143,144,145,146,147,148,149,150,151,152,153,154,155,156,157,158) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


(238970, 186)

In [4]:
liwc_attr = ['X1funct' ,'X2pronoun' ,'X3ppron','X4i','X5we','X6you','X7shehe','X8they','X9ipron','X10article','X11verb','X12auxverb','X13past','X14present','X15future','X16adverb','X17preps','X18conj','X19negate','X20quant','X21number','X22swear','X23social','X24family','X25friend','X26humans','X27affect','X28posemo','X29negemo','X30anx','X31anger','X32sad','X33cogmech','X34insight','X35cause','X36discrep','X37tentat','X38certain','X39inhib','X40incl','X41excl','X42percept','X43see','X44hear','X45feel','X46bio','X47body','X48health','X49sexual','X50ingest','X51relativ','X52motion','X53space','X54time','X55work','X56achieve','X57leisure','X58home','X59money','X60relig','X61death','X62assent','X63nonfl', 'X64filler']

In [5]:
df = df.convert_objects(convert_numeric=True)

/usr/lib/python2.7/site-packages/ipykernel/__main__.py:1: FutureWarning: convert_objects is deprecated.  Use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  if __name__ == '__main__':


In [6]:
psico = pd.read_csv('/home/bahbbc/Downloads/psycholinguistic_properties/BP.csv', encoding='utf-8')

In [7]:
psico.head()

Word Simplified grammatical category  Concretenes  \
0     abafado                               a         3.47   
1    abafador                               a         5.73   
2     abalado                               a         2.61   
3   abalizado                               a         3.88   
4  abandonado                               a         3.68   

   Subjective Frequency  Imagery   AoA  Log frequency  Frequency  
0                  3.92     3.96  5.28           7.11     1220.0  
1                  2.84     5.10  7.25           4.41       82.0  
2                  4.12     3.59  7.62           8.15     3450.0  
3                  2.58     3.56  7.59           4.36       78.0  
4                  4.16     3.97  5.24           9.75    17183.0

In [8]:
concreteness = dict(zip(psico.Word, psico.Concretenes))
subjective_freq = dict(zip(psico.Word, psico['Subjective Frequency']))
imagery = dict(zip(psico.Word, psico.Imagery))
aoa =  dict(zip(psico.Word, psico.AoA))
log_freq = dict(zip(psico.Word, psico['Log frequency']))
freq = dict(zip(psico.Word, psico.Frequency))

In [9]:
df.extraversion_m.value_counts()

0    121670
1    117300
Name: extraversion_m, dtype: int64

In [10]:
train_w2v_data, test_w2v_data = train_test_split(df, test_size=0.3, random_state=42)

In [11]:
def remove_nan(atributes):
    train_attr = np.array(train_w2v_data[atributes])
    test_attr = np.array(test_w2v_data[atributes])
    train_attr[np.isnan(train_attr)] = 0
    test_attr[np.isnan(test_attr)] = 0
    return (train_attr, test_attr)

In [12]:
def predict(vectorizer, classifier, data):
    data_features = vectorizer.transform(data['formatted_text'])
    predictions = classifier.predict(data_features)
    target = data['extraversion_m']
    evaluate_prediction(predictions, target)

In [13]:
def makeFeatureVec(words, psico_dict):
    # Function to average all of the word vectors in a given
    # paragraph
    #
    # Pre-initialize an empty numpy array (for speed)
    featureVec = 0.
    #
    nwords = 0.
    
    #
    # Loop over each word in the review and, if it is in the model's
    # vocaublary, add its feature vector to the total
    for word in words:
        if (word in psico_dict):
            nwords = nwords + 1.
            featureVec = featureVec + psico_dict[word]
    # 
    # Divide the result by the number of words to get the average
    if nwords > 0:
        featureVec = featureVec / nwords
    else:
        print 'sorry, empty...'
    return featureVec


def getAvgFeatureVecs(reviews, psico_dict):
    # Given a set of reviews (each one a list of words), calculate 
    # the average feature vector for each one and return a 2D numpy array 
    # 
    # Initialize a counter
    counter = 0
    # 
    # Preallocate a 2D numpy array, for speed
    reviewFeatureVecs = np.zeros((len(reviews)),dtype="float32")
    # 
    # Loop through the reviews
    for review in reviews:
        #Print a status message every 1000th review
        if counter%100. == 0.:
            print "Review %d of %d" % (counter, len(reviews))
        #Call the function (defined above) that makes average feature vectors
        reviewFeatureVecs[counter] = makeFeatureVec(review, psico_dict)
        #Increment the counter
        counter = counter + 1
    return reviewFeatureVecs

In [14]:
def w2v_tokenize_text(text):
    tokens = []
    if text is np.nan:
        return []
    for sent in nltk.sent_tokenize(text, language='portuguese'):
        for word in nltk.word_tokenize(sent, language='portuguese'):
            word = word.lower()
            if len(word) < 2:
                continue
            tokens.append(word)
    return tokens

In [15]:
train, test = remove_nan(liwc_attr)

In [16]:
test_tokenized = test_w2v_data.apply(lambda r: w2v_tokenize_text(r['formatted_text']), axis=1).values
train_tokenized = train_w2v_data.apply(lambda r: w2v_tokenize_text(r['formatted_text']), axis=1).values

In [17]:
index = pd.isnull(train_w2v_data.formatted_text)
train_w2v_data.loc[index, 'formatted_text'] = ''

/usr/lib64/python2.7/site-packages/pandas/core/indexing.py:477: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [18]:
concreteness = dict(zip(psico.Word, psico.Concretenes))
subjective_freq = dict(zip(psico.Word, psico['Subjective Frequency']))
imagery = dict(zip(psico.Word, psico.Imagery))
aoa =  dict(zip(psico.Word, psico.AoA))
log_freq = dict(zip(psico.Word, psico['Log frequency']))
freq = dict(zip(psico.Word, psico.Frequency))

In [19]:
conc_trainDataVecs = getAvgFeatureVecs( train_tokenized, concreteness )
conc_testDataVecs = getAvgFeatureVecs( test_tokenized, concreteness )
sub_trainDataVecs = getAvgFeatureVecs( train_tokenized, subjective_freq )
sub_testDataVecs = getAvgFeatureVecs( test_tokenized, subjective_freq )
ima_trainDataVecs = getAvgFeatureVecs( train_tokenized, imagery )
ima_testDataVecs = getAvgFeatureVecs( test_tokenized, imagery )
aoa_trainDataVecs = getAvgFeatureVecs( train_tokenized, aoa )
aoa_testDataVecs = getAvgFeatureVecs( test_tokenized, aoa )

Review 0 of 167279
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
Review 100 of 167279
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...
sorry, empty...


In [20]:
train_data = np.vstack((conc_trainDataVecs,sub_trainDataVecs, ima_trainDataVecs, aoa_trainDataVecs))

In [21]:
train_data = train_data.T
train_data = pd.DataFrame(train_data, index=train_w2v_data.index, columns=['concreteness', 'subjective_freq', 'imagery', 'aoa'])
train = pd.DataFrame(train, index=train_w2v_data.index, columns=liwc_attr)

In [22]:
train_features = pd.concat([train_data, train], axis=1)

In [23]:
test_data = np.vstack((conc_testDataVecs, sub_testDataVecs, ima_testDataVecs, aoa_testDataVecs))

In [24]:
test_data = test_data.T
test_data = pd.DataFrame(test_data, index=test_w2v_data.index, columns=['concreteness', 'subjective_freq', 'imagery', 'aoa'])
test = pd.DataFrame(test, index=test_w2v_data.index, columns=liwc_attr)

In [25]:
test_features = pd.concat([test_data, test], axis=1)

# Correlation heatmap

In [26]:
correlation_attr = train_features.append(test_features)

extr = train_w2v_data.extraversion.append(test_w2v_data.extraversion)
agre = train_w2v_data.agreeableness.append(test_w2v_data.agreeableness)
cons = train_w2v_data.conscientiousness.append(test_w2v_data.conscientiousness)
neur = train_w2v_data.neuroticism.append(test_w2v_data.neuroticism)
openn = train_w2v_data.openness.append(test_w2v_data.openness)

personality_data = pd.DataFrame({'extr': extr, 'agre':agre, 'cons':cons, 'neur':neur, 'open':openn})

correlation_attr = pd.concat([correlation_attr, personality_data], axis=1)

In [27]:
corr = correlation_attr.corr()

In [28]:
corr['extr'][abs(corr['extr']) > 0.2]

X24family    0.200734
X28posemo    0.218339
extr         1.000000
open         0.215956
Name: extr, dtype: float64

In [29]:
corr['agre'][abs(corr['agre']) > 0.15]

X27affect    0.150022
X28posemo    0.194398
agre         1.000000
cons         0.184472
extr         0.193474
neur        -0.348070
Name: agre, dtype: float64

In [30]:
corr['cons'][abs(corr['cons']) > 0.15]

X28posemo    0.181192
X54time      0.155339
agre         0.184472
cons         1.000000
extr         0.155086
Name: cons, dtype: float64

In [31]:
corr['neur'][abs(corr['neur']) > 0.15]

X4i     0.172642
agre   -0.348070
extr   -0.163381
neur    1.000000
Name: neur, dtype: float64

In [32]:
corr['open'][abs(corr['open']) > 0.15]

extr    0.215956
open    1.000000
Name: open, dtype: float64

In [ ]:
# Generate a mask for the upper triangle
mask = np.zeros_like(corr, dtype=np.bool)
mask[np.triu_indices_from(mask)] = True

In [ ]:
# Set up the matplotlib figure
f, ax = plt.subplots(figsize=(21, 19))

# Generate a custom diverging colormap
cmap = sns.diverging_palette(220, 10, as_cmap=True)

# Draw the heatmap with the mask and correct aspect ratio
sns.heatmap(corr, mask=mask, cmap=cmap, vmax=.3, center=0,
            square=True, linewidths=.5, cbar_kws={"shrink": .5})

In [ ]:
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier

force = False
model_trainer = RandomizedSearchCV(
    n_iter=1, 
    estimator=RandomForestClassifier(),
    param_distributions={
        "criterion": ["gini"],
        "n_estimators": [1000],
        "max_features": ["log2"],
        "max_depth": [None],
        "bootstrap": [True],
        "oob_score": [True],
        "class_weight": ["balanced"],
        "random_state": [42]
    },
    scoring="f1",
    verbose=True,
    refit=True,
    cv=10,
    n_jobs=-1
)

## Extraversion

In [ ]:
%%time
model_trainer.fit(train_features, train_w2v_data['extraversion_m'])
model = model_trainer.best_estimator_

In [ ]:
yp = model.predict(test_features)
yt = test_w2v_data['extraversion_m']

In [ ]:
pd.DataFrame(
    index=pd.Index([0, 1], name="y_true"),
    columns=pd.Index([0, 1], name="y_pred"),
    data=skmetrics.confusion_matrix(y_true=yt, y_pred=yp)
)

In [ ]:
print skmetrics.classification_report(y_true=yt, y_pred=yp)

In [ ]:
accuracy_score(yt, yp)

In [ ]:
print '--------- TRAIN -----------------'

In [ ]:
ytp = model.predict(train_features)
ytt = train_w2v_data['extraversion_m']

In [ ]:
print skmetrics.classification_report(y_true=ytt, y_pred=ytp)

In [ ]:
print accuracy_score(ytt, ytp)

In [ ]:
names = test_features.keys()
print "Features sorted by their score:"
print sorted(zip(map(lambda x: round(x, 4), model.feature_importances_), names), 
             reverse=True)

In [ ]:
features = test_features.keys()
importances = model.feature_importances_

indices = np.argsort(importances)[-10:]

plt.title('Importancia dos atributos')
plt.barh(range(len(indices)), importances[indices], color='b', align='center')
plt.yticks(range(len(indices)), features[indices]) ## removed [indices]
plt.xlabel('Importancia relativa')
plt.show()

## Agreableness

In [ ]:
%%time
model_trainer.fit(train_features, train_w2v_data['agreeabeness_m'])
model = model_trainer.best_estimator_

In [ ]:
yp = model.predict(test_features)
yt = test_w2v_data['agreeabeness_m']

In [ ]:
pd.DataFrame(
    index=pd.Index([0, 1], name="y_true"),
    columns=pd.Index([0, 1], name="y_pred"),
    data=skmetrics.confusion_matrix(y_true=yt, y_pred=yp)
)

In [ ]:
print skmetrics.classification_report(y_true=yt, y_pred=yp)

In [ ]:
accuracy_score(yt, yp)

In [ ]:
names = test_features.keys()
print "Features sorted by their score:"
print sorted(zip(map(lambda x: round(x, 4), model.feature_importances_), names), 
             reverse=True)

In [ ]:
features = test_features.keys()
importances = model.feature_importances_

indices = np.argsort(importances)[-10:]

plt.title('Importancia dos atributos')
plt.barh(range(len(indices)), importances[indices], color='b', align='center')
plt.yticks(range(len(indices)), features[indices]) ## removed [indices]
plt.xlabel('Importancia relativa')
plt.show()

## Conscientiousness

In [ ]:
%%time
model_trainer.fit(train_features, train_w2v_data['conscientiousness_m'])
model = model_trainer.best_estimator_

In [ ]:
yp = model.predict(test_features)
yt = test_w2v_data['conscientiousness_m']

In [ ]:
pd.DataFrame(
    index=pd.Index([0, 1], name="y_true"),
    columns=pd.Index([0, 1], name="y_pred"),
    data=skmetrics.confusion_matrix(y_true=yt, y_pred=yp)
)

In [ ]:
print skmetrics.classification_report(y_true=yt, y_pred=yp)

In [ ]:
accuracy_score(yt, yp)

In [ ]:
names = test_features.keys()
print "Features sorted by their score:"
print sorted(zip(map(lambda x: round(x, 4), model.feature_importances_), names), 
             reverse=True)

In [ ]:
features = test_features.keys()
importances = model.feature_importances_

indices = np.argsort(importances)[-10:]

plt.title('Importancia dos atributos')
plt.barh(range(len(indices)), importances[indices], color='b', align='center')
plt.yticks(range(len(indices)), features[indices]) ## removed [indices]
plt.xlabel('Importancia relativa')
plt.show()

## Neuroticism

In [ ]:
%%time
model_trainer.fit(train_features, train_w2v_data['neuroticism_m'])
model = model_trainer.best_estimator_

In [ ]:
yp = model.predict(test_features)
yt = test_w2v_data['neuroticism_m']

In [ ]:
pd.DataFrame(
    index=pd.Index([0, 1], name="y_true"),
    columns=pd.Index([0, 1], name="y_pred"),
    data=skmetrics.confusion_matrix(y_true=yt, y_pred=yp)
)

In [ ]:
print skmetrics.classification_report(y_true=yt, y_pred=yp)

In [ ]:
accuracy_score(yt, yp)

In [ ]:
names = test_features.keys()
print "Features sorted by their score:"
print sorted(zip(map(lambda x: round(x, 4), model.feature_importances_), names), 
             reverse=True)

In [ ]:
features = test_features.keys()
importances = model.feature_importances_

indices = np.argsort(importances)[-10:]

plt.title('Importancia dos atributos')
plt.barh(range(len(indices)), importances[indices], color='b', align='center')
plt.yticks(range(len(indices)), features[indices]) ## removed [indices]
plt.xlabel('Importancia relativa')
plt.show()

## Openess

In [ ]:
%%time
model_trainer.fit(train_features, train_w2v_data['openness_m'])
model = model_trainer.best_estimator_

In [ ]:
yp = model.predict(test_features)
yt = test_w2v_data['openness_m']

In [ ]:
pd.DataFrame(
    index=pd.Index([0, 1], name="y_true"),
    columns=pd.Index([0, 1], name="y_pred"),
    data=skmetrics.confusion_matrix(y_true=yt, y_pred=yp)
)

In [ ]:
print skmetrics.classification_report(y_true=yt, y_pred=yp)

In [ ]:
accuracy_score(yt, yp)

In [ ]:
names = test_features.keys()
print "Features sorted by their score:"
print sorted(zip(map(lambda x: round(x, 4), model.feature_importances_), names), 
             reverse=True)

In [ ]:
features = test_features.keys()
importances = model.feature_importances_

indices = np.argsort(importances)[-10:]

plt.title('Importancia dos atributos')
plt.barh(range(len(indices)), importances[indices], color='b', align='center')
plt.yticks(range(len(indices)), features[indices]) ## removed [indices]
plt.xlabel('Importancia relativa')
plt.show()